## Lab 1

### Part 1

### Import Libraries

In [98]:
from bs4 import BeautifulSoup
import requests
import pandas as pd
import re
import random

In [99]:
#attribute url
url = "https://www.popvortex.com/music/charts/top-100-songs.php"

In [100]:
#get request
response = requests.get(url)
response.status_code

200

In [101]:
soup = BeautifulSoup(response.content, "html.parser")

In [102]:
#divide the different criteria into a different lists to be put into our final dataframe

artist = []
song = []
genre = []
year = []

num_iter = len("body > div.container > div:nth-child(4) > div.col-xs-12.col-md-8 > div.chart-wrapper > div.feed-item")

songart = soup.select("body > div.container > div:nth-child(4) > div.col-xs-12.col-md-8 > div.chart-wrapper > div.feed-item")
genlist = soup.select("body > div.container > div:nth-child(4) > div.col-xs-12.col-md-8 > div.chart-wrapper > div.feed-item > div.chart-content")
yearlist = soup.select("body > div.container > div:nth-child(4) > div.col-xs-12.col-md-8 > div.chart-wrapper > div.feed-item > div.chart-content > ul > li:nth-child(2)")

for i in range(num_iter):
    artist.append(songart[i].em.get_text())
    song.append(songart[i].cite.get_text())
    year.append(yearlist[i].get_text())    
    try:
        genre.append(genlist[i].ul.li.a.get_text())
    except:
        genre.append('Unknown')

    

In [103]:
#Attribute the lists to a dataframe

top100 = pd.DataFrame({'artist':artist
                    ,'track':song
                    ,'genre':genre
                    ,'year':year})

In [104]:
top100

artist                                   track        genre  \
0           Lizzo                         About Damn Time          Pop   
1       Kate Bush  Running Up That Hill (A Deal with God)          Pop   
2            P!nk                              Irrelevant  New Release   
3        Slipknot           The Dying Song (Time To Sing)  New Release   
4    Walker Hayes                              Y'all Life  New Release   
..            ...                                     ...          ...   
95          Drake           Jimmy Cooks (feat. 21 Savage)        Dance   
96  One Direction                           Night Changes          Pop   
97  Glass Animals                              Heat Waves  Alternative   
98       Dua Lipa               Levitating (feat. DaBaby)          Pop   
99         j-hope                                What If…  New Release   

                               year  
0      Release Date: April 14, 2022  
1      Release Date: August 5, 1985  
2                        Genre: Pop  
3                Genre: Heavy Metal  
4                    Genre: Country  
..                              ...  
95      Release Date: June 17, 2022  
96  Release Date: November 17, 2014  
97      Release Date: June 29, 2020  
98    Release Date: October 1, 2020  
99                     Genre: K-Pop  

[100 rows x 4 columns]

In [105]:
#In the year column we have a Genre: leak. We will split these genres...  

def genresplit(value):
    if 'Genre:' in value:
        name = value.split('Genre: ')[1]
        
        return name
    else:
        return value

In [106]:
#...move these genres 
top100['genre'] = top100['genre'].apply(genresplit)
top100['year'] = top100['year'].apply(genresplit)

In [107]:
def tidy(value):

    type1 = value['genre']
    type2 = value['year']
    if str(type1) == 'New Release':
        return type2
    else:
        return type1

    
top100['genre'] = top100.apply(tidy,axis=1)

In [108]:
#finally split the year column by the comma and find the year value. "Nan" values filled with 2022, because it was originally a "New Release" value
top100['year'] = top100['year'].str.split(", ", n = 1, expand = True)[1]
top100['year'] = top100['year'].fillna(2022)
top100['track'] = top100['track'].str.strip()

In [109]:
top100

artist                                   track        genre  year
0           Lizzo                         About Damn Time          Pop  2022
1       Kate Bush  Running Up That Hill (A Deal with God)          Pop  1985
2            P!nk                              Irrelevant          Pop  2022
3        Slipknot           The Dying Song (Time To Sing)  Heavy Metal  2022
4    Walker Hayes                              Y'all Life      Country  2022
..            ...                                     ...          ...   ...
95          Drake           Jimmy Cooks (feat. 21 Savage)        Dance  2022
96  One Direction                           Night Changes          Pop  2014
97  Glass Animals                              Heat Waves  Alternative  2020
98       Dua Lipa               Levitating (feat. DaBaby)          Pop  2020
99         j-hope                                What If…        K-Pop  2022

[100 rows x 4 columns]

### Part 2

In [110]:
urls = "https://spinditty.com/playlists/100songs"

In [111]:
responses = requests.get(urls)
responses.status_code

200

In [112]:
sopa = BeautifulSoup(responses.content, "html.parser")

In [113]:
##attribute different values to song, artist, genre and year lists. 

songartist2 = []
genre2 = []
years2 = []
num_iter = len("body > div.container > div:nth-child(4) > div.col-xs-12.col-md-8 > div.chart-wrapper > div.feed-item")

songarts = sopa.select("body > phoenix-page > div > div > div.m-page > section > article > div > div > section > div > div > h2")
genres = sopa.select("body > phoenix-page > div > div > div.m-page > section > article > div > div > section > div > div > p")
years = sopa.select("body > phoenix-page > div > div > div.m-page > section > article > div > div > section > div > div > h3")
for i in range(len(songarts)):
    songartist2.append(songarts[i].get_text())
    
for i in range(len(genres)):
    genre2.append(genres[i].get_text())
        
for i in range(len(years)):
    years2.append(years[i].get_text())


In [114]:
##find genre in text. 

genrefin = []
for i in genre2:
    if 'Genre:' in i:
        genrefin.append(i)
    elif 'GENRE:' in i:
        genrefin.append(i)

        
##filter any unneeded rows. 

songartfin = []        
for j in songartist2:
    if '#' in j:
        songartfin.append(j)
        

#treat values longer than years
lap = []
for i in years2:
    if len(i) > 4:
        i = re.findall('\d{4}',i)
        lap.append(i)
    else:
        lap.append(i)
years2 = lap

In [115]:
#drop any duplicates, then create the dataframe for table2 

top100s = pd.DataFrame({'go':songartfin})
top100s = top100s.drop_duplicates().reset_index()
top100s = pd.DataFrame({'go': top100s['go'], 'genre':genrefin, 'year':years2})

In [116]:
top100s

go  \
0         #100 - "Bitter Sweet Symphony" by The Verve   
1   #99: "For What It's Worth" by Buffalo Springfield   
2                 #98 "Fire and Rain" by James Taylor   
3                 #97: "Rolling in the Deep" by Adele   
4   #96 "(We're Gonna) Rock Around the Clock" by B...   
..                                                ...   
95                           #5: "Stairway to Heaven"   
96                       #4: "Imagine" by John Lennon   
97            #3: "Like a Rolling Stone" by Bob Dylan   
98                     #2: "Yesterday" by The Beatles   
99               #1: "Johnny B. Goode" by Chuck Berry   

                      genre    year  
0            Genre: Britpop  [1997]  
1          Genre: Folk Rock    1967  
2          Genre: Folk Rock  [1970]  
3                Genre: Pop  [2011]  
4        Genre: Rock & Roll    1954  
..                      ...     ...  
95              Genre: Rock  [1971]  
96              Genre: Rock  [1971]  
97         Genre: Folk Rock  [1965]  
98  Genre: British Invasion  [1965]  
99       Genre: Rock & Roll  [1959]  

[100 rows x 3 columns]

In [117]:
#determine artist, genre and track columns, as well as year cleaning. 

top100s['track'] = top100s['go'].str.split("by", n = 1, expand = True)[0]
top100s['artist'] = top100s['go'].str.split("by", n = 1, expand = True)[1]
top100s['track'] = top100s['track'].str.split('"', n = 1, expand = True)[1]
top100s['genre'] = top100s['genre'].str.split(': ', n = 1, expand = True)[1]
top100s['track'] = top100s['track'].str.replace('"','')

yearconvert = []

#if it's a list:
for i in top100s['year']:
    if isinstance(i,list):
        yearconvert.append(i[0])
    else:
        yearconvert.append(i)

top100s['year'] = yearconvert

top100s['track'] = top100s['track'].str.strip()

In [118]:
top100s = top100s[['track','artist','genre','year']]

In [119]:
top100s

track                      artist  \
0                 Bitter Sweet Symphony                   The Verve   
1                   For What It's Worth         Buffalo Springfield   
2                         Fire and Rain                James Taylor   
3                   Rolling in the Deep                       Adele   
4   (We're Gonna) Rock Around the Clock   Bill Haley and His Comets   
..                                  ...                         ...   
95                   Stairway to Heaven                        None   
96                              Imagine                 John Lennon   
97                 Like a Rolling Stone                   Bob Dylan   
98                            Yesterday                 The Beatles   
99                      Johnny B. Goode                 Chuck Berry   

               genre  year  
0            Britpop  1997  
1          Folk Rock  1967  
2          Folk Rock  1970  
3                Pop  2011  
4        Rock & Roll  1954  
..               ...   ...  
95              Rock  1971  
96              Rock  1971  
97         Folk Rock  1965  
98  British Invasion  1965  
99       Rock & Roll  1959  

[100 rows x 4 columns]

In [120]:
#concatenate into one table
top100s = top100s[['track','artist','genre','year']]
top100 = top100[['track','artist','genre','year']]
top = pd.concat([top100,top100s], axis = 0).reset_index()
top = top.drop(columns='index')

In [121]:
top

track        artist             genre  \
0                           About Damn Time         Lizzo               Pop   
1    Running Up That Hill (A Deal with God)     Kate Bush               Pop   
2                                Irrelevant          P!nk               Pop   
3             The Dying Song (Time To Sing)      Slipknot       Heavy Metal   
4                                Y'all Life  Walker Hayes           Country   
..                                      ...           ...               ...   
195                      Stairway to Heaven          None              Rock   
196                                 Imagine   John Lennon              Rock   
197                    Like a Rolling Stone     Bob Dylan         Folk Rock   
198                               Yesterday   The Beatles  British Invasion   
199                         Johnny B. Goode   Chuck Berry       Rock & Roll   

     year  
0    2022  
1    1985  
2    2022  
3    2022  
4    2022  
..    ...  
195  1971  
196  1971  
197  1965  
198  1965  
199  1959  

[200 rows x 4 columns]

## Lab 2

In [122]:
def musicrecommender():
    song = input("Name of your song: ")    
    if song in list(top['track']):
        print(top['track'].iloc[random.randint(0,200)])    
    elif song not in list(top['track']):
        print("Sorry, we cannot recommend any songs")

In [123]:
musicrecommender()

Name of your song: Yesterday
Sweet Caroline


## Lab 3

In [124]:
import spotipy
from spotipy.oauth2 import SpotifyClientCredentials

In [125]:
secrets_file = open("/Users/chrislacarte/Desktop/IRONHACK/W6/3/6.5 API Wrappers, SpotiPy/secrets.txt","r")

In [126]:
string = secrets_file.read()
string.split('\n')

['cid:4a238c496d454d91a9a37f6c037aa38a',
 'csecret:1f0d681218f44443bfa47de795570426']

In [127]:
secrets_dict={}
for line in string.split('\n'):
    if len(line) > 0:
        secrets_dict[line.split(':')[0]]=line.split(':')[1]

In [128]:
import spotipy
from spotipy.oauth2 import SpotifyClientCredentials

#InitializeSpotiPy with user credentials
sp = spotipy.Spotify(auth_manager=SpotifyClientCredentials(client_id=secrets_dict['cid'],
                                                           client_secret=secrets_dict['csecret']))

In [129]:
#playlist1 = sp.user_playlist_tracks("spotify", "6tIxyT1Gq6O7DK7rIEUEZo")
#playlist2 = sp.user_playlist_tracks("spotify", "4pbDDX7np7Q1H0ghL7U9o7")

In [130]:
from random import randint
from time import sleep

def get_playlist_tracks(playlist_id):
    results = sp.user_playlist_tracks("spotify",playlist_id)
    tracks = results['items']
    while results['next']!=None:
        results = sp.next(results)
        tracks = tracks + results['items']
        sleep(randint(1,3))
    return tracks

In [151]:
all_tracks1 = get_playlist_tracks("6tIxyT1Gq6O7DK7rIEUEZo")
all_tracks2 = get_playlist_tracks("4pbDDX7np7Q1H0ghL7U9o7")


In [145]:
playlist1 = all_tracks1
playlist2 = all_tracks2

In [153]:
playlist1

[{'added_at': '2022-07-20T13:43:15Z',
  'added_by': {'external_urls': {'spotify': 'https://open.spotify.com/user/dudewheresmybass89'},
   'href': 'https://api.spotify.com/v1/users/dudewheresmybass89',
   'id': 'dudewheresmybass89',
   'type': 'user',
   'uri': 'spotify:user:dudewheresmybass89'},
  'is_local': False,
  'primary_color': None,
  'track': {'album': {'album_type': 'album',
    'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/1dfeR4HaWDbWqFHLkxsg1d'},
      'href': 'https://api.spotify.com/v1/artists/1dfeR4HaWDbWqFHLkxsg1d',
      'id': '1dfeR4HaWDbWqFHLkxsg1d',
      'name': 'Queen',
      'type': 'artist',
      'uri': 'spotify:artist:1dfeR4HaWDbWqFHLkxsg1d'}],
    'available_markets': ['AD',
     'AE',
     'AG',
     'AL',
     'AM',
     'AO',
     'AR',
     'AT',
     'AU',
     'AZ',
     'BA',
     'BB',
     'BD',
     'BE',
     'BF',
     'BG',
     'BH',
     'BI',
     'BJ',
     'BN',
     'BO',
     'BR',
     'BS',
     'BT',
     '

In [146]:
print('no. 1    ',len(all_tracks1))
print('no. 2    ',len(all_tracks2))
print('total is',len(all_tracks1)+len(all_tracks2))

no. 1     9999
no. 2     3878
total is 13877


In [157]:
def artistsong(pops):
    artist = []
    song = []
    features = []
    counter = 0
    for i in pops:
        song.append(pops[counter]['track']['name'])
        artist.append(pops[counter]['track']['artists'][0]['name'])
        features.append(sp.audio_features(pops[counter]["track"]["uri"]))
        counter += 1
    return pd.DataFrame({'artist': artist, 'song': song, 'features': features})

In [158]:
import pandas as pd
playlist1df = artistsong(playlist1)
playlist2df = artistsong(playlist2)

Expected id of type track but found type A%C3%AFcha spotify:local:Khaled:Sahra:A%C3%AFcha:259
Expected id of type track but found type Kids+In+America spotify:local:Kim+Wilde:Simply+The+Best+Of+The+80%27s:Kids+In+America:202
Expected id of type track but found type La+Bamba spotify:local:Los+Lobos:The+Best+Latino+Carnival+In+The+World+...+Ever%21+%28Disc+1%29:La+Bamba:171
Expected id of type track but found type Live+Is+Life spotify:local:Opus:Simply+The+Best+Of+The+80%27s:Live+Is+Life:244
Expected id of type track but found type All+Night+Long spotify:local:Lionel+Richie:Can%27t+Slow+Down:All+Night+Long:379
Expected id of type track but found type %28Keep+Feeling%29+Fascination spotify:local:The+Human+League:Grand+Theft+Auto%3A+Vice+City%2C+Vol.+2%3A+Wave+103:%28Keep+Feeling%29+Fascination:222
Expected id of type track but found type More+Than+This spotify:local:Roxy+Music:Grand+Theft+Auto%3A+Vice+City%2C+Vol.+3%3A+Emotion+98.3:More+Than+This:266
Expected id of type track but found ty

In [159]:
playlist1df

artist                                          song  \
0          Queen             A Kind Of Magic - Remastered 2011   
1          Queen           Bohemian Rhapsody - Remastered 2011   
2          Queen  Another One Bites The Dust - Remastered 2011   
3          Queen           Don't Stop Me Now - Remastered 2011   
4          Queen              Under Pressure - Remastered 2011   
...          ...                                           ...   
9994  Kip Winger         California - From the Moon to the Sun   
9995  Kip Winger        What We Are - From the Moon to the Sun   
9996  Kip Winger       One Big Game - From the Moon to the Sun   
9997  Kip Winger                Why - From the Moon to the Sun   
9998  Kip Winger  Reason to Believe - From the Moon to the Sun   

                                               features  
0     [{'danceability': 0.67, 'energy': 0.776, 'key'...  
1     [{'danceability': 0.414, 'energy': 0.404, 'key...  
2     [{'danceability': 0.933, 'energy': 0.528, 'key...  
3     [{'danceability': 0.559, 'energy': 0.868, 'key...  
4     [{'danceability': 0.671, 'energy': 0.712, 'key...  
...                                                 ...  
9994  [{'danceability': 0.517, 'energy': 0.444, 'key...  
9995  [{'danceability': 0.476, 'energy': 0.721, 'key...  
9996  [{'danceability': 0.542, 'energy': 0.7, 'key':...  
9997  [{'danceability': 0.27, 'energy': 0.561, 'key'...  
9998  [{'danceability': 0.652, 'energy': 0.825, 'key...  

[9999 rows x 3 columns]

In [160]:
playlist2df

artist                        song  \
0             ANGRA              Live and Learn   
1             ANGRA              Bleeding Heart   
2             ANGRA            Hunters and Prey   
3             ANGRA              Eyes of Christ   
4             ANGRA  Rebirth (Acoustic Version)   
...             ...                         ...   
3873  Fleetwood Mac                  Family Man   
3874  Fleetwood Mac  Welcome To The Room...Sara   
3875  Fleetwood Mac           Isn't It Midnight   
3876  Fleetwood Mac        When I See You Again   
3877  Fleetwood Mac          You And I, Part II   

                                               features  
0     [{'danceability': 0.431, 'energy': 0.984, 'key...  
1     [{'danceability': 0.5, 'energy': 0.545, 'key':...  
2     [{'danceability': 0.56, 'energy': 0.892, 'key'...  
3     [{'danceability': 0.512, 'energy': 0.937, 'key...  
4     [{'danceability': 0.348, 'energy': 0.596, 'key...  
...                                                 ...  
3873  [{'danceability': 0.688, 'energy': 0.644, 'key...  
3874  [{'danceability': 0.632, 'energy': 0.555, 'key...  
3875  [{'danceability': 0.469, 'energy': 0.73, 'key'...  
3876  [{'danceability': 0.544, 'energy': 0.0907, 'ke...  
3877  [{'danceability': 0.69, 'energy': 0.627, 'key'...  

[3878 rows x 3 columns]

In [169]:
playlist1_flat['features']= json_normalize(playlist1df['features'])
playlist2_flat['features'] = json_normalize(playlist2df['features'])

/var/folders/hq/x_513gjd2qsd86w2rwvd665m0000gn/T/ipykernel_12180/656307236.py:1: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  playlist1_flat['features']= json_normalize(playlist1df['features'])
/var/folders/hq/x_513gjd2qsd86w2rwvd665m0000gn/T/ipykernel_12180/656307236.py:2: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  playlist2_flat['features'] = json_normalize(playlist2df['features'])


In [170]:
playlist1_flat['features']

0       {'danceability': 0.67, 'energy': 0.776, 'key':...
1       {'danceability': 0.414, 'energy': 0.404, 'key'...
2       {'danceability': 0.933, 'energy': 0.528, 'key'...
3       {'danceability': 0.559, 'energy': 0.868, 'key'...
4       {'danceability': 0.671, 'energy': 0.712, 'key'...
                              ...                        
9994    {'danceability': 0.517, 'energy': 0.444, 'key'...
9995    {'danceability': 0.476, 'energy': 0.721, 'key'...
9996    {'danceability': 0.542, 'energy': 0.7, 'key': ...
9997    {'danceability': 0.27, 'energy': 0.561, 'key':...
9998    {'danceability': 0.652, 'energy': 0.825, 'key'...
Name: features, Length: 9999, dtype: object

In [178]:
playlist1_fin = pd.DataFrame.from_records(playlist1_flat.features.dropna().tolist())
playlist2_fin = pd.DataFrame.from_records(playlist2_flat.features.dropna().tolist())

In [185]:
playlist1_flat = playlist1_flat.reset_index(drop = True)
playlist1_fin  = playlist1_fin.reset_index(drop = True)
playlist_db1 = pd.concat([playlist1_flat,playlist1_fin], axis = 1)
playlist_db1

artist                                          song  \
0          Queen             A Kind Of Magic - Remastered 2011   
1          Queen           Bohemian Rhapsody - Remastered 2011   
2          Queen  Another One Bites The Dust - Remastered 2011   
3          Queen           Don't Stop Me Now - Remastered 2011   
4          Queen              Under Pressure - Remastered 2011   
...          ...                                           ...   
9994  Kip Winger         California - From the Moon to the Sun   
9995  Kip Winger        What We Are - From the Moon to the Sun   
9996  Kip Winger       One Big Game - From the Moon to the Sun   
9997  Kip Winger                Why - From the Moon to the Sun   
9998  Kip Winger  Reason to Believe - From the Moon to the Sun   

                                               features  danceability  energy  \
0     {'danceability': 0.67, 'energy': 0.776, 'key':...         0.670   0.776   
1     {'danceability': 0.414, 'energy': 0.404, 'key'...         0.414   0.404   
2     {'danceability': 0.933, 'energy': 0.528, 'key'...         0.933   0.528   
3     {'danceability': 0.559, 'energy': 0.868, 'key'...         0.559   0.868   
4     {'danceability': 0.671, 'energy': 0.712, 'key'...         0.671   0.712   
...                                                 ...           ...     ...   
9994  {'danceability': 0.517, 'energy': 0.444, 'key'...         0.517   0.444   
9995  {'danceability': 0.476, 'energy': 0.721, 'key'...         0.476   0.721   
9996  {'danceability': 0.542, 'energy': 0.7, 'key': ...         0.542   0.700   
9997  {'danceability': 0.27, 'energy': 0.561, 'key':...         0.270   0.561   
9998  {'danceability': 0.652, 'energy': 0.825, 'key'...         0.652   0.825   

       key  loudness  mode  speechiness  acousticness  ...  liveness  valence  \
0      9.0    -5.874   1.0       0.0356        0.0184  ...    0.1280    0.703   
1      0.0    -9.928   0.0       0.0499        0.2710  ...    0.3000    0.224   
2      5.0    -6.472   0.0       0.1610        0.1120  ...    0.1630    0.754   
3      5.0    -5.276   1.0       0.1700        0.0475  ...    0.7760    0.609   
4      2.0    -7.815   1.0       0.0476        0.4290  ...    0.1030    0.462   
...    ...       ...   ...          ...           ...  ...       ...      ...   
9994   0.0   -12.046   0.0       0.0267        0.5550  ...    0.1320    0.216   
9995   0.0    -7.143   1.0       0.0335        0.1000  ...    0.4070    0.470   
9996   5.0    -7.395   0.0       0.0359        0.0669  ...    0.0850    0.403   
9997   2.0    -8.061   0.0       0.0351        0.5370  ...    0.1970    0.151   
9998  10.0    -6.932   0.0       0.0513        0.1490  ...    0.0339    0.740   

        tempo            type                      id  \
0     130.128  audio_features  5RYLa5P4qweEAKq5U1gdcK   
1      71.105  audio_features  4u7EnebtmKWzUH433cf5Qv   
2     109.967  audio_features  5vdp5UmvTsnMEMESIF2Ym7   
3     156.295  audio_features  5T8EDUDqKcs6OSOwEsfqG7   
4     113.805  audio_features  2fuCquhmrzHpu5xcA1ci9x   
...       ...             ...                     ...   
9994  187.950  audio_features  2STE3vIHHIgz9TNB5aJGC1   
9995   86.987  audio_features  3pQJKvK6hmVPzDXRv67PCo   
9996  153.999  audio_features  03P0IMmk5nXRyrhh0YpTfc   
9997  140.047  audio_features  70Hf4cnE286JKpi3lwRb1w   
9998   94.970  audio_features  3eHox3muLGkKxUGgUfy3mH   

                                       uri  \
0     spotify:track:5RYLa5P4qweEAKq5U1gdcK   
1     spotify:track:4u7EnebtmKWzUH433cf5Qv   
2     spotify:track:5vdp5UmvTsnMEMESIF2Ym7   
3     spotify:track:5T8EDUDqKcs6OSOwEsfqG7   
4     spotify:track:2fuCquhmrzHpu5xcA1ci9x   
...                                    ...   
9994  spotify:track:2STE3vIHHIgz9TNB5aJGC1   
9995  spotify:track:3pQJKvK6hmVPzDXRv67PCo   
9996  spotify:track:03P0IMmk5nXRyrhh0YpTfc   
9997  spotify:track:70Hf4cnE286JKpi3lwRb1w   
9998  spotify:track:3eHox3muLGkKxUGgUfy3mH   

                                 

In [186]:
playlist2_flat = playlist2_flat.reset_index(drop = True)
playlist2_fin  = playlist2_fin.reset_index(drop = True)
playlist_db2 = pd.concat([playlist2_flat,playlist2_fin], axis = 1)
playlist_db2

artist                        song  \
0             ANGRA              Live and Learn   
1             ANGRA              Bleeding Heart   
2             ANGRA            Hunters and Prey   
3             ANGRA              Eyes of Christ   
4             ANGRA  Rebirth (Acoustic Version)   
...             ...                         ...   
3873  Fleetwood Mac                  Family Man   
3874  Fleetwood Mac  Welcome To The Room...Sara   
3875  Fleetwood Mac           Isn't It Midnight   
3876  Fleetwood Mac        When I See You Again   
3877  Fleetwood Mac          You And I, Part II   

                                               features  danceability  energy  \
0     {'danceability': 0.431, 'energy': 0.984, 'key'...         0.431  0.9840   
1     {'danceability': 0.5, 'energy': 0.545, 'key': ...         0.500  0.5450   
2     {'danceability': 0.56, 'energy': 0.892, 'key':...         0.560  0.8920   
3     {'danceability': 0.512, 'energy': 0.937, 'key'...         0.512  0.9370   
4     {'danceability': 0.348, 'energy': 0.596, 'key'...         0.348  0.5960   
...                                                 ...           ...     ...   
3873  {'danceability': 0.688, 'energy': 0.644, 'key'...         0.688  0.6440   
3874  {'danceability': 0.632, 'energy': 0.555, 'key'...         0.632  0.5550   
3875  {'danceability': 0.469, 'energy': 0.73, 'key':...         0.469  0.7300   
3876  {'danceability': 0.544, 'energy': 0.0907, 'key...         0.544  0.0907   
3877  {'danceability': 0.69, 'energy': 0.627, 'key':...         0.690  0.6270   

      key  loudness  mode  speechiness  acousticness  ...  liveness  valence  \
0       1    -5.131     1       0.0907       0.00591  ...    0.0650    0.167   
1      10    -7.115     1       0.0277       0.16500  ...    0.3670    0.118   
2       2    -6.740     1       0.0366       0.00286  ...    0.1020    0.679   
3       8    -5.403     1       0.0467       0.06220  ...    0.0792    0.469   
4       9    -7.498     0       0.0291       0.50100  ...    0.1110    0.343   
...   ...       ...   ...          ...           ...  ...       ...      ...   
3873    7   -12.733     1       0.0360       0.02070  ...    0.1070    0.918   
3874    7   -13.081     0       0.0409       0.11400  ...    0.2600    0.732   
3875    0   -11.890     0       0.0358       0.00264  ...    0.1500    0.573   
3876   11   -20.015     0       0.0268       0.87200  ...    0.1030    0.103   
3877    9   -14.645     1       0.0363       0.06310  ...    0.0848    0.956   

        tempo            type                      id  \
0     144.996  audio_features  5LZci9wxIwwvF9qh8cMpHS   
1     123.974  audio_features  4m2HvlrZ1kKsgFpcLh5h0V   
2     114.986  audio_features  3Gs5F9IN5BEhU8jhdr5KrQ   
3     105.021  audio_features  2ahYaznOR2pfAu6voMj3T7   
4      74.179  audio_features  3tQWuqbfcQumQL3KHfOM3C   
...       ...             ...                     ...   
3873  123.350  audio_features  7FaarqLNsZlFsRMQjjX5QR   
3874   99.064  audio_features  5H1EXMKjBFlI5F9QkCD6Ft   
3875  145.781  audio_features  2icOTC7sCLZSDVbCPJ6olG   
3876   79.789  audio_features  0QE9gbtUuiSJIqclW9N2TQ   
3877  123.438  audio_features  01pmYrV2NrQBivoGxXjzl3   

                                       uri  \
0     spotify:track:5LZci9wxIwwvF9qh8cMpHS   
1     spotify:track:4m2HvlrZ1kKsgFpcLh5h0V   
2     spotify:track:3Gs5F9IN5BEhU8jhdr5KrQ   
3     spotify:track:2ahYaznOR2pfAu6voMj3T7   
4     spotify:track:3tQWuqbfcQumQL3KHfOM3C   
...                                    ...   
3873  spotify:track:7FaarqLNsZlFsRMQjjX5QR   
3874  spotify:track:5H1EXMKjBFlI5F9QkCD6Ft   
3875  spotify:track:2icOTC7sCLZSDVbCPJ6olG   
3876  spotify:track:0QE9gbtUuiSJIqclW9N2TQ   
3877  spotify:track:01pmYrV2NrQBivoGxXjzl3   

                                             track_href  \
0     https://api.spotify.com/v1/tracks/5LZci9wxIwwv...   
1     https://api.spotify.com/v1/tracks/4m2HvlrZ1kKs...   
2     https://api.spotify.com/v1/tracks/3Gs5F9IN5BE

In [189]:
final_1 = playlist_db1.drop(columns = 'features')
final_2 =playlist_db2.drop(columns = 'features')

In [192]:
final_1


artist                                          song  danceability  \
0          Queen             A Kind Of Magic - Remastered 2011         0.670   
1          Queen           Bohemian Rhapsody - Remastered 2011         0.414   
2          Queen  Another One Bites The Dust - Remastered 2011         0.933   
3          Queen           Don't Stop Me Now - Remastered 2011         0.559   
4          Queen              Under Pressure - Remastered 2011         0.671   
...          ...                                           ...           ...   
9994  Kip Winger         California - From the Moon to the Sun         0.517   
9995  Kip Winger        What We Are - From the Moon to the Sun         0.476   
9996  Kip Winger       One Big Game - From the Moon to the Sun         0.542   
9997  Kip Winger                Why - From the Moon to the Sun         0.270   
9998  Kip Winger  Reason to Believe - From the Moon to the Sun         0.652   

      energy   key  loudness  mode  speechiness  acousticness  \
0      0.776   9.0    -5.874   1.0       0.0356        0.0184   
1      0.404   0.0    -9.928   0.0       0.0499        0.2710   
2      0.528   5.0    -6.472   0.0       0.1610        0.1120   
3      0.868   5.0    -5.276   1.0       0.1700        0.0475   
4      0.712   2.0    -7.815   1.0       0.0476        0.4290   
...      ...   ...       ...   ...          ...           ...   
9994   0.444   0.0   -12.046   0.0       0.0267        0.5550   
9995   0.721   0.0    -7.143   1.0       0.0335        0.1000   
9996   0.700   5.0    -7.395   0.0       0.0359        0.0669   
9997   0.561   2.0    -8.061   0.0       0.0351        0.5370   
9998   0.825  10.0    -6.932   0.0       0.0513        0.1490   

      instrumentalness  liveness  valence    tempo            type  \
0             0.002940    0.1280    0.703  130.128  audio_features   
1             0.000000    0.3000    0.224   71.105  audio_features   
2             0.312000    0.1630    0.754  109.967  audio_features   
3             0.000176    0.7760    0.609  156.295  audio_features   
4             0.000000    0.1030    0.462  113.805  audio_features   
...                ...       ...      ...      ...             ...   
9994          0.000940    0.1320    0.216  187.950  audio_features   
9995          0.000122    0.4070    0.470   86.987  audio_features   
9996          0.006750    0.0850    0.403  153.999  audio_features   
9997          0.000640    0.1970    0.151  140.047  audio_features   
9998          0.000196    0.0339    0.740   94.970  audio_features   

                          id                                   uri  \
0     5RYLa5P4qweEAKq5U1gdcK  spotify:track:5RYLa5P4qweEAKq5U1gdcK   
1     4u7EnebtmKWzUH433cf5Qv  spotify:track:4u7EnebtmKWzUH433cf5Qv   
2     5vdp5UmvTsnMEMESIF2Ym7  spotify:track:5vdp5UmvTsnMEMESIF2Ym7   
3     5T8EDUDqKcs6OSOwEsfqG7  spotify:track:5T8EDUDqKcs6OSOwEsfqG7   
4     2fuCquhmrzHpu5xcA1ci9x  spotify:track:2fuCquhmrzHpu5xcA1ci9x   
...                      ...                                   ...   
9994  2STE3vIHHIgz9TNB5aJGC1  spotify:track:2STE3vIHHIgz9TNB5aJGC1   
9995  3pQJKvK6hmVPzDXRv67PCo  spotify:track:3pQJKvK6hmVPzDXRv67PCo   
9996  03P0IMmk5nXRyrhh0YpTfc  spotify:track:03P0IMmk5nXRyrhh0YpTfc   
9997  70Hf4cnE286JKpi3lwRb1w  spotify:track:70Hf4cnE286JKpi3lwRb1w   
9998  3eHox3muLGkKxUGgUfy3mH  spotify:track:3eHox3muLGkKxUGgUfy3mH   

                                             track_href  \
0     https://api.spotify.com/v1/tracks/5RYLa5P4qweE...   
1     https://api.spotify.com/v1/tracks/4u7EnebtmKWz...   
2     https://api.spotify.com/v1/tracks/5vdp5UmvTsnM...   
3     https://api.spotify.com/v1/tracks/5T8EDUDqKcs6...   
4     https://api.spotify.com/v1/tracks/2fuCquhmrzHp...   
...                                                 ...   
9994  https://api.spotify.com/v1/tracks/2STE3vIHHIgz...   
9995  https://api.spotify.com/v1/tracks/3pQJKvK6hmVP...   
9996  https://api.spotify.com/v1/tracks/03P0IMmk5nXR...

In [190]:
final_2

artist                        song  danceability  energy  key  \
0             ANGRA              Live and Learn         0.431  0.9840    1   
1             ANGRA              Bleeding Heart         0.500  0.5450   10   
2             ANGRA            Hunters and Prey         0.560  0.8920    2   
3             ANGRA              Eyes of Christ         0.512  0.9370    8   
4             ANGRA  Rebirth (Acoustic Version)         0.348  0.5960    9   
...             ...                         ...           ...     ...  ...   
3873  Fleetwood Mac                  Family Man         0.688  0.6440    7   
3874  Fleetwood Mac  Welcome To The Room...Sara         0.632  0.5550    7   
3875  Fleetwood Mac           Isn't It Midnight         0.469  0.7300    0   
3876  Fleetwood Mac        When I See You Again         0.544  0.0907   11   
3877  Fleetwood Mac          You And I, Part II         0.690  0.6270    9   

      loudness  mode  speechiness  acousticness  instrumentalness  liveness  \
0       -5.131     1       0.0907       0.00591          0.000003    0.0650   
1       -7.115     1       0.0277       0.16500          0.000000    0.3670   
2       -6.740     1       0.0366       0.00286          0.002030    0.1020   
3       -5.403     1       0.0467       0.06220          0.000003    0.0792   
4       -7.498     0       0.0291       0.50100          0.000000    0.1110   
...        ...   ...          ...           ...               ...       ...   
3873   -12.733     1       0.0360       0.02070          0.007750    0.1070   
3874   -13.081     0       0.0409       0.11400          0.000003    0.2600   
3875   -11.890     0       0.0358       0.00264          0.048200    0.1500   
3876   -20.015     0       0.0268       0.87200          0.000000    0.1030   
3877   -14.645     1       0.0363       0.06310          0.000019    0.0848   

      valence    tempo            type                      id  \
0       0.167  144.996  audio_features  5LZci9wxIwwvF9qh8cMpHS   
1       0.118  123.974  audio_features  4m2HvlrZ1kKsgFpcLh5h0V   
2       0.679  114.986  audio_features  3Gs5F9IN5BEhU8jhdr5KrQ   
3       0.469  105.021  audio_features  2ahYaznOR2pfAu6voMj3T7   
4       0.343   74.179  audio_features  3tQWuqbfcQumQL3KHfOM3C   
...       ...      ...             ...                     ...   
3873    0.918  123.350  audio_features  7FaarqLNsZlFsRMQjjX5QR   
3874    0.732   99.064  audio_features  5H1EXMKjBFlI5F9QkCD6Ft   
3875    0.573  145.781  audio_features  2icOTC7sCLZSDVbCPJ6olG   
3876    0.103   79.789  audio_features  0QE9gbtUuiSJIqclW9N2TQ   
3877    0.956  123.438  audio_features  01pmYrV2NrQBivoGxXjzl3   

                                       uri  \
0     spotify:track:5LZci9wxIwwvF9qh8cMpHS   
1     spotify:track:4m2HvlrZ1kKsgFpcLh5h0V   
2     spotify:track:3Gs5F9IN5BEhU8jhdr5KrQ   
3     spotify:track:2ahYaznOR2pfAu6voMj3T7   
4     spotify:track:3tQWuqbfcQumQL3KHfOM3C   
...                                    ...   
3873  spotify:track:7FaarqLNsZlFsRMQjjX5QR   
3874  spotify:track:5H1EXMKjBFlI5F9QkCD6Ft   
3875  spotify:track:2icOTC7sCLZSDVbCPJ6olG   
3876  spotify:track:0QE9gbtUuiSJIqclW9N2TQ   
3877  spotify:track:01pmYrV2NrQBivoGxXjzl3   

                                             track_href  \
0     https://api.spotify.com/v1/tracks/5LZci9wxIwwv...   
1     https://api.spotify.com/v1/tracks/4m2HvlrZ1kKs...   
2     https://api.spotify.com/v1/tracks/3Gs5F9IN5BEh...   
3     https://api.spotify.com/v1/tracks/2ahYaznOR2pf...   
4     https://api.spotify.com/v1/tracks/3tQWuqbfcQum...   
...                                                 ...   
3873  https://api.spotify.com/v1/tracks/7FaarqLNsZlF...   
3874  https://api.spotify.com/v1/tracks/5H1EXMKjBFlI...   
3875  https://api.spotify.com/v1/tracks/2icOTC7sCLZS...   
3876  https://api.spotify.com/v1/tracks/0QE9gbtUuiSJ...   
3877  https://api.spotify.com/v1/tracks/01pmYrV2NrQB...   

                                           analysis_url  duration_ms  \


In [193]:
final_1 = final_1.reset_index(drop = True)
final_2 = final_2.reset_index(drop = True)
final_p = pd.concat([final_1,final_2], axis = 0)
final_p

artist                                          song  \
0             Queen             A Kind Of Magic - Remastered 2011   
1             Queen           Bohemian Rhapsody - Remastered 2011   
2             Queen  Another One Bites The Dust - Remastered 2011   
3             Queen           Don't Stop Me Now - Remastered 2011   
4             Queen              Under Pressure - Remastered 2011   
...             ...                                           ...   
3873  Fleetwood Mac                                    Family Man   
3874  Fleetwood Mac                    Welcome To The Room...Sara   
3875  Fleetwood Mac                             Isn't It Midnight   
3876  Fleetwood Mac                          When I See You Again   
3877  Fleetwood Mac                            You And I, Part II   

      danceability  energy   key  loudness  mode  speechiness  acousticness  \
0            0.670  0.7760   9.0    -5.874   1.0       0.0356       0.01840   
1            0.414  0.4040   0.0    -9.928   0.0       0.0499       0.27100   
2            0.933  0.5280   5.0    -6.472   0.0       0.1610       0.11200   
3            0.559  0.8680   5.0    -5.276   1.0       0.1700       0.04750   
4            0.671  0.7120   2.0    -7.815   1.0       0.0476       0.42900   
...            ...     ...   ...       ...   ...          ...           ...   
3873         0.688  0.6440   7.0   -12.733   1.0       0.0360       0.02070   
3874         0.632  0.5550   7.0   -13.081   0.0       0.0409       0.11400   
3875         0.469  0.7300   0.0   -11.890   0.0       0.0358       0.00264   
3876         0.544  0.0907  11.0   -20.015   0.0       0.0268       0.87200   
3877         0.690  0.6270   9.0   -14.645   1.0       0.0363       0.06310   

      instrumentalness  liveness  valence    tempo            type  \
0             0.002940    0.1280    0.703  130.128  audio_features   
1             0.000000    0.3000    0.224   71.105  audio_features   
2             0.312000    0.1630    0.754  109.967  audio_features   
3             0.000176    0.7760    0.609  156.295  audio_features   
4             0.000000    0.1030    0.462  113.805  audio_features   
...                ...       ...      ...      ...             ...   
3873          0.007750    0.1070    0.918  123.350  audio_features   
3874          0.000003    0.2600    0.732   99.064  audio_features   
3875          0.048200    0.1500    0.573  145.781  audio_features   
3876          0.000000    0.1030    0.103   79.789  audio_features   
3877          0.000019    0.0848    0.956  123.438  audio_features   

                          id                                   uri  \
0     5RYLa5P4qweEAKq5U1gdcK  spotify:track:5RYLa5P4qweEAKq5U1gdcK   
1     4u7EnebtmKWzUH433cf5Qv  spotify:track:4u7EnebtmKWzUH433cf5Qv   
2     5vdp5UmvTsnMEMESIF2Ym7  spotify:track:5vdp5UmvTsnMEMESIF2Ym7   
3     5T8EDUDqKcs6OSOwEsfqG7  spotify:track:5T8EDUDqKcs6OSOwEsfqG7   
4     2fuCquhmrzHpu5xcA1ci9x  spotify:track:2fuCquhmrzHpu5xcA1ci9x   
...                      ...                                   ...   
3873  7FaarqLNsZlFsRMQjjX5QR  spotify:track:7FaarqLNsZlFsRMQjjX5QR   
3874  5H1EXMKjBFlI5F9QkCD6Ft  spotify:track:5H1EXMKjBFlI5F9QkCD6Ft   
3875  2icOTC7sCLZSDVbCPJ6olG  spotify:track:2icOTC7sCLZSDVbCPJ6olG   
3876  0QE9gbtUuiSJIqclW9N2TQ  spotify:track:0QE9gbtUuiSJIqclW9N2TQ   
3877  01pmYrV2NrQBivoGxXjzl3  spotify:track:01pmYrV2NrQBivoGxXjzl3   

                                             track_href  \
0     https://api.spotify.com/v1/tracks/5RYLa5P4qweE...   
1     https://api.spotify.com/v1/tracks/4u7EnebtmKWz...   
2     https://api.spotify.com/v1/tracks/5vdp5UmvTsnM...   
3     https://api.spotify.com/v1/tracks/5T8EDUDqKcs6...   
4     https://api.spotify.com/v1/tracks/2fuCquhmrzHp...   
...                                                 ...   
3873  https://api.spotify.com/v1/tracks/7FaarqLNsZlF...   
3874  https://api.spotify.com/v1/tracks/5H1EXMKjBFlI...   
3875  https://api.spot